In [31]:
import json
from collections import OrderedDict
import re
import sys, os, platform, subprocess
import functools, httplib, urllib2, socket
from threading import Thread
from time import sleep
from multiprocessing import Process, Pipe
import struct

class BoundHTTPHandler(urllib2.HTTPHandler):
	def __init__(self, source_address=None, debuglevel=0):
		urllib2.HTTPHandler.__init__(self, debuglevel)
		self.http_class = functools.partial(httplib.HTTPConnection,
				source_address=source_address)
	def http_open(self, req):
		return self.do_open(self.http_class, req)
    

class Camera():
    def __init__(self,ind):
        self.index = ind
        self.ip = "10.5.5.%d"%(ind+100)
        self.opener = urllib2.build_opener(BoundHTTPHandler(source_address=(self.ip, 0)))
        self.isAlive = False
    def SendUrlCmd(self,url):
        
        #print "sending gopro %d: \n"%self.index
        try:
            result = self.opener.open(url, timeout=4).read()
            return result
        except Exception,e:
            print str(e)
        #print "sending finished \n"
        
    def RegisterMac(self,macaddr):
        self.mac = macaddr
    def GetMac(self):
        text = self.SendUrlCmd("http://10.5.5.9/videos/MISC/version.txt")
        return text[74:86]
    def Wake(self):
        macaddress = self.mac
        data = ''.join(['FFFFFFFFFFFF', macaddress * 20])
        send_data = ''
        # Split up the hex values and pack.
        for i in range(0, len(data), 2):
            send_data = ''.join([send_data,struct.pack('B', int(data[i: i + 2], 16))])
        # Broadcast it to the LAN.
        sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
        sock.setsockopt(socket.SOL_SOCKET, socket.SO_BROADCAST, 1)
        sock.bind((self.ip,8080))
        sock.sendto(send_data, ('10.5.5.9', 9))
        sock.shutdown(socket.SHUT_RDWR)
        sock.close()
    def Sleep(self):
        self.SendUrlCmd("http://10.5.5.9/gp/gpControl/command/system/sleep")
    def GetLastImg(self,path):
        print "Transsferring Gopro%d:\n"%self.index
        campath = os.path.join(path,"Cam%d"%self.index)
        if not os.path.exists(campath):
            os.mkdir(campath)
        rawlist = json.loads(self.SendUrlCmd("http://10.5.5.9:8080/gp/gpMediaList"))['media'][0]
        filelist = rawlist['fs']
        filename = filelist[-1]['n']
        dirname = rawlist['d']
        print filename
        data = self.SendUrlCmd("http://10.5.5.9:8080/videos/DCIM/%s/"%dirname+filename)
        with open(os.path.join(campath,filename),'wb') as target:
            target.write(data)
        print("finished.")
    def CopyAllMultiShotFiles(self,path):
        rawlist = json.loads(self.SendUrlCmd("http://10.5.5.9:8080/gp/gpMediaList"))['media'][0]
        gpfilepath = "http://10.5.5.9:8080/videos/DCIM/%s/"%rawlist['d']
        for data in rawlist['fs']:
            if data.has_key('g') and data.has_key('b') and data.has_key('l'):
                tmppathroot = os.path.join(path,"batch%d"%int(data['g']))
                print "  Transferring Batch%d(%s-%s):\n"%(int(data['g']),data['b'],data['l'])
                if not os.path.exists(tmppathroot):
                    os.mkdir(tmppathroot)
                tmppath = os.path.join(tmppathroot,"Cam%d"%self.index)
                if not os.path.exists(tmppath):
                    os.mkdir(tmppath)
                for fid in range(int(data['b']),int(data['l'])+1):
                    filename = "G%03d%d.JPG"%(int(data['g']),fid)
                    rawpic = self.SendUrlCmd(gpfilepath+filename)
                    print filename
                    with open(os.path.join(tmppath,filename),'wb') as target:
                        target.write(rawpic)
                    print "    "+filename+"Transffered."
                print "  Batch%d(%s-%s) Transfered.\n"%(int(data['g']),data['b'],data['l'])

class CameraArrayCommand():
    def __init__(self):
        return
    def RegisterMacs(self,camarr,macmap):
        for cam in camarr:
            mac = macmap["GoproNumber%d"%cam.index]
            cam.RegisterMac(mac)
    def SetControl(self,camarr,url):
        for cam in camarr:
            try:
                cam.SendUrlCmd(url)
            except Exception,e:
                print "cam%d"%cam.index+" failed:"+str(e)
                continue
    def Wake(self,camarray):
        for cam in camarray:
            try:
                cam.Wake()
            except Exception,e:
                print "cam%d"%cam.index+" failed:"+str(e)
                continue
    def Sleep(self,camarray):
        for cam in camarray:
            try:
                cam.Sleep()
            except Exception,e:
                print "cam%d"%cam.index+" failed:"+str(e)
                continue
    def GetLastImage(self,camarray):
        for cam in camarray:
            cam.GetLastImg("D:\gopro_multiview_gui")
        
    
def ReadJson(path):
    cmd_file_name = 'command.json'
    js = load_json(os.path.join(path,cmd_file_name))

    cmddict = dict()
    try:
        cmddict["controls"] = js['controls']
        cmddict["mac_map"] = js['mac_map']
    except Exception, e:
        print str(e)
        exit()
    return cmddict
        
        
def StartFFplay(cam):
        prefix = "ffplay -fflags nobuffer -f:v mpegts -probesize 8192 udp://"
        print prefix + "%s?localaddr=%s" % (cam.ip, cam.ip)
        os.system(prefix + "%s:8554?localaddr=%s" % (cam.ip, cam.ip))

def KeepAliveSingle(cam):
    MESSAGE = "_GPHD_:%u:%u:%d:%1lf\n" % (0, 0, 2, 0)
    UDP_IP = "10.5.5.9"
    UDP_PORT = 8554
    KEEP_ALIVE_PERIOD = 2500
    if sys.version_info.major >= 3:
        MESSAGE = bytes(MESSAGE, "utf-8")
    while True:
        sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
        sock.bind((cam.ip,8080))
        sock.sendto(MESSAGE, (UDP_IP, UDP_PORT))
        sock.close()
    sleep(KEEP_ALIVE_PERIOD/1000)

def LoadJson(path):
    with open(path,'r') as datasource:
        data = json.load(datasource)
    return data
        

In [14]:
cmddict = LoadJson('D:/gopro_multiview_gui/newcommand.json')

In [32]:
cam4 = Camera(4)

In [35]:
cam4.SendUrlCmd('http://10.5.5.9:8080/videos/DCIM/100GOPRO/G0010328.JPG')

'\xff\xd8\xff\xe1\xc1\x0cExif\x00\x00MM\x00*\x00\x00\x00\x08\x00\x0b\x01\x0e\x00\x02\x00\x00\x00\x18\x00\x00\x03\xf4\x01\x0f\x00\x02\x00\x00\x00\x1e\x00\x00\x04\x0c\x01\x10\x00\x02\x00\x00\x00\x1e\x00\x00\x04*\x01\x12\x00\x03\x00\x00\x00\x01\x00\x01\x00\x00\x01\x1a\x00\x05\x00\x00\x00\x01\x00\x00\x04H\x01\x1b\x00\x05\x00\x00\x00\x01\x00\x00\x04P\x01(\x00\x03\x00\x00\x00\x01\x00\x02\x00\x00\x011\x00\x02\x00\x00\x00\x18\x00\x00\x04X\x012\x00\x02\x00\x00\x00\x14\x00\x00\x04p\x02\x13\x00\x03\x00\x00\x00\x01\x00\x01\x00\x00\x87i\x00\x04\x00\x00\x00\x01\x00\x00\x00\x92\x00\x00\x02\x96\x00(\x82\x9a\x00\x05\x00\x00\x00\x01\x00\x00\x04\x84\x82\x9d\x00\x05\x00\x00\x00\x01\x00\x00\x04\x8c\x88"\x00\x03\x00\x00\x00\x01\x00\x02\x00\x00\x88\'\x00\x03\x00\x00\x00\x01\x00\xb3\x00\x00\x90\x00\x00\x07\x00\x00\x00\x040221\x90\x03\x00\x02\x00\x00\x00\x14\x00\x00\x04\x94\x90\x04\x00\x02\x00\x00\x00\x14\x00\x00\x04\xa8\x91\x01\x00\x07\x00\x00\x00\x04\x01\x02\x03\x00\x91\x02\x00\x05\x00\x00\x00\x01\x00\x00\x0

In [34]:
cam4.CopyAllMultiShotFiles('D:/data/')

  Transferring Batch1(328-345):

HTTP Error 404: Not Found
G001328.JPG


TypeError: must be string or buffer, not None

In [46]:
cam1.

'G002'

In [58]:
out = cam1.SendUrlCmd(cmddict['FilePath'])

sending gopro 1: 

sending finished 



In [80]:
a={'1234':4,'a':1,'asdfdsgf':2,'zzz':1}

In [81]:
sorted(a)

['1234', 'a', 'asdfdsgf', 'zzz']

In [ ]:
cam